# Incremental WCM

## Word Context Matrix


The Word Context Matrix is widely used for constructing count-based word representations in static environments. The matrix has dimensions V x C, where V represents the vocabulary size, and C represents the number of context words. If the vocabulary of the target and context words is the same, the dimensionality of the matrix becomes |V| × |V|. The context words are selected based on their proximity to a vocabulary word in a sliding window, the size of which is determined by the user and can range from 1 to 8 surrounding words.

For instance, given the sentence "the dog barked very loudly," with the vocabulary word "barked," the context words would be "the" and "dog" on the left and "very" and "loudly" on the right if the window length were set to 2.

The relationship between a vocabulary word and its context words is weighted using various strategies, including co-occurrence counts, positive point-wise mutual information (PPMI), and paired t-test values. The most commonly used measure among the three is PPMI, which filters conventional PMI values by setting negative values to zero and calculates the logarithm of the joint probability of a vocabulary word and its context over the probability of their occurrence independently.  The following image illustrates how the matrix is built from the three examples sentences considering a sliding window of 1.

![alt](../static/wcm.png)

## Incremental Word Context Matrix

The implementation of incremental word embedding using the PPMI weight must consider the following important considerations:

* One-time processing: Each line of text or tweet is processed only once and discarded after that.

* Incremental calculation of probabilities: The probabilities of the PPMI must be calculated incrementally, requiring memory to store the intermediate results.

* Adaptation to a streaming setting: The algorithm must be flexible enough to adapt to a streaming setting, where the vocabulary and context words may be unknown in advance.

These considerations are crucial for building an effective incremental word embedding model using the PPMI method. The model's performance and accuracy depend on how well these considerations are addressed and implemented in the algorithm.

In terms of the hyperparameters, it is essential to consider the size of the vocabulary (V), the size of the contexts (C), and the size of the sliding window (W). These hyperparameters have a direct impact on the dimensionality of the incremental Word Context matrix, which is restricted to V x C, and is not necessarily square. The careful selection and tuning of these hyperparameters can help to achieve optimal performance and accuracy in the word embedding model.

![alt](../static/alg-wcm.png)

In our implementation, a sliding window of 2W tokens is used to extract context information from the tokenized tweets in the text stream. The center of the window aligns with a target word, and all surrounding tokens within the window are considered context tokens. When a target word or context is encountered for the first time, a new entry is dynamically created in the VectorDict objects and initialized with a count value of zero. When an existing target word or context is encountered, the corresponding counters are updated incrementally. This approach allows for efficient storage and manipulation of the word-context matrix while maintaining an acceptable level of accuracy.

However, one limitation of this method is that, like its static counterpart, the IWCM model produces sparse and high-dimensional vectors. To address this issue, we use incremental Principal Component Analysis (PCA) to reduce the dimensionality of the generated embeddings. This algorithm processes the data as a vector stream, so it doesn't require multiple passes over the entire set of embeddings to achieve dimensionality reduction. In addition, our IWCM implementation selectively applies dimensionality reduction to recently added or updated embedding vectors to optimize computational efficiency.

### import libraries

In [9]:
from rivertext.utils import TweetStream
from torch.utils.data import DataLoader

from rivertext.models import WordContextMatrix

### Define the Stream

In [10]:
ts = TweetStream("tweets.txt")
dataloader = DataLoader(ts, batch_size=32)

### Define the model

In [11]:
wcm = WordContextMatrix(
    vocab_size=1_000_000,
    window_size=3,
    context_size=500
)

### Training loop

In [12]:
for tweet in dataloader:
    wcm.learn_many(tweet)

### Getting the embeddings

In [13]:
embs = wcm.vocab2dict()

{'gluetext': array([[ 5.15143352e-01,  5.78664107e-02, -4.87970636e-01,
         -6.92767319e-01, -2.44620188e-01, -2.43482195e-01,
          9.23132878e-02, -8.46130685e-02,  1.97235200e-02,
          1.92075200e-02, -2.86320453e-01,  1.17146412e-01,
          3.84857586e-01,  7.77580545e-01, -3.51926728e-02,
         -8.85696516e-01,  2.53327360e-01, -1.29691897e-01,
         -2.35884431e-01,  4.41828487e-01, -1.06229261e-02,
          2.58170431e-01,  8.12654912e-02,  8.49311867e-02,
         -1.98160529e-01, -3.46979341e-01, -1.27702664e-01,
          8.03462474e-03, -3.09755827e-01, -6.33336076e-02,
         -4.84941051e-02,  6.95087008e-02, -2.77192188e-01,
          1.99546333e-03,  1.89173561e-01, -4.86372442e-02,
          8.01682979e-02,  1.13440160e-01, -1.15472534e-01,
          2.41293591e-01,  2.78143432e-01,  1.33704256e-01,
          3.48676169e-02,  1.72813302e-01,  1.95370013e-01,
         -2.02512827e-01, -8.38958554e-02,  6.74269925e-02,
         -9.52183883e-03,  2

In [ ]:
embs['gluetext']